# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model
(Recurrent PPO) [default: 25 EVs per week simulation]

Installing required packages and dependencies

In [64]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [65]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

fatal: destination path 'RL_VPP_Thesis' already exists and is not an empty directory.
/content/RL_VPP_Thesis/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_simulator.ipynb
data/                             Simulator_notebooks/  wandb/
Hyperparameters_sweep_notebooks/  trained_models/
log.log                           VPP_environment.py


In [66]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.15
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.15', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.15\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [67]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [68]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f814362e750>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [69]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [70]:
env.plot_ELVIS_data()

In [71]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  20493.14 , Grid_used_en=kWh  38267.63 , RE-to-vehicle_unused_en=kWh  17774.48 , Total_selling_cost=€  876.89 , Grid_cost=€  1397.36 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [72]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [73]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [74]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [75]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [76]:
env.plot_VPP_Elvis_comparison()

In [77]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [78]:
#env.plot_rewards_stats()

In [79]:
env.plot_EVs_kpi()

In [80]:
env.plot_actions_kpi()

In [81]:
env.plot_load_kpi()

In [82]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [83]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [84]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



## Testing dataset VPP Simulation using the loaded trained model

In [85]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21755.88 , Grid_used_en=kWh  39240.86 , RE-to-vehicle_unused_en=kWh  17484.99 , Total_selling_cost=€  910.09 , Grid_cost=€  1408.9 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4295.55 , Grid_used_en=KWh  1950.77 , RE-to-vehicle_unused_en=KWh  6246.32 , Total_selling_cost=€  -74.53 , Grid_cost=€  73.31 
 EV_INFO: Av.EV_energy_leaving=kWh  65.87 , Std.EV_energy_leaving=kWh  24.07 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 400255.64 - Step_rewars (load_t= 366635.74, EVs_energy_t= 12361.59)
 - Final_rewards (Av.EVs_energy= 15306.3, Grid_used_en= -1212.77, RE-to-vehicle_unused_en= -2948.24, Grid_cost= 10113.02)
Episode:1 Score:400255.63706556056


In [86]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [87]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  47.018578  48.063133   0.000000  57.296120   
2022-01-01 00:15:00  47.268578  46.955185   0.000000  57.546120   
2022-01-01 00:30:00  47.518578  46.491177   0.000000  57.082111   
2022-01-01 00:45:00  47.768578  46.159611   0.000000  56.750546   
2022-01-01 01:00:00  48.018578  45.788944   0.000000  56.379879   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00   0.000000  68.934471  52.675621  63.383312   
2022-06-06 05:00:00   0.000000  70.004898  53.746044  64.453735   
2022-06-06 05:15:00   0.000000  71.147728  54.888878  65.596565   
2022-06-06 05:30:00   0.000000  72.162018  55.903172  66.610855   
2022-06-06 05:45:00   0.000000  73.083282  56.824436  67.532120   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [13559, 13558, 0, 13557]  [1, 2, 2, 2]   
2022-01-01 00:30:00  [13559, 13558, 0, 13557]  [1, 2, 2, 2]   
2022-01-01 00:45:00  [13559, 13558, 0, 13557]  [1, 2, 2, 2]   
2022-01-01 01:00:00  [13559, 13558, 0, 13557]  [1, 2, 2, 2]   
...                                       ...           ...   
2022-06-06 04:45:00  [0, 13989, 13988, 13990]  [2, 1, 1, 1]   
2022-06-06 05:00:00  [0, 13989, 13988, 13990]  [2, 1, 1, 1]   
2022-06-06 05:15:00  [0, 13989, 13988, 13990]  [2, 1, 1, 1]   
2022-06-06 05:30:00  [0, 13989, 13988, 13990]  [2, 1, 1, 1]   
2022-06-06 05:45:00  [0, 13989, 13988, 13990]  [2, 1, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00    [False, True, False, True]        2.000000   
2022-01-01 00:30:00    [False, True, False, True]        1.000000   
2022-01-01 00:45:00    [False, True, False, True]        1.000000   
2022-01-01 01:00:00    [False, True, False, True]        1.000000   
...                                           ...             ...   
2022-06-06 04:45:00     [False, True, True, True]        9.476428   
2022-06-06 05:00:00     [False, True, True, True]       12.845099   
2022-06-06 05:15:00     [False, True, True, True]       13.713999   
2022-06-06 05:30:00     [False, True, True, True]       12.171512   
2022-06-06 05:45:00     [False, True, True, True]       11.055178   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  9.137659e-01    15.000000        0.0   
2022-01-01 00:15:00          -4.431787 -4.440892e-16    15.000000        0.0   
2022-01-01 00:30:00          -3.712062  0.000000e+00    15.000000        0.0   
2022-01-01 00:45:00          -2.652526  0.000000e+00    15.000000        0.0   
2022-01-01 01:00:00          -2.965344 -2.220446e-16    11.297548        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00           0.000000  0.000000e+00    15.000000        0.0   
2022-06-06 05:00:00           0.000000 -1.776357e-15    15.000000        0.0   
2022-06-06 05:15:00           0.000000  1.776357e-15    15.000000        0.0   
2022-06-06 05:30:00           0.000000  0.000000e+00    15.000000        0.0   
2022-06-06 05:45:00           0.000000  0.000000e+00    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  15.000000  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  11.297548  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
20

In [88]:
#env.plot_Elvis_results()

In [89]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [90]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [91]:
env.plot_VPP_Elvis_comparison()

In [92]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [93]:
env.plot_rewards_stats()

In [94]:
env.plot_EVs_kpi()

In [95]:
env.plot_load_kpi()

In [96]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [97]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 14603, Arrival time: 2022-01-01 10:30:00, Parking_time: 24, Leaving_time: 2022-01-02 10:30:00, SOC: 0.39306688442302695, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 15645, Arrival time: 2022-12-31 19:30:00, Parking_time: 22.952116817928047, Leaving_time: 2023-01-01 18:27:07.620545, SOC: 0.513027085199917, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en=kWh  2136.67 , RE-to-vehicle_unused_en=kWh  -32222.06 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12746.53 , Grid_used_en=kWh  34501.58 , RE-to-vehicle_unused_en=kWh  21755.05 , Total_selling_cost=€  626.75 , Grid_cost=€  1513.19 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [98]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [99]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [100]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12950.08 , Grid_used_en=kWh  34868.22 , RE-to-vehicle_unused_en=kWh  21918.14 , Total_selling_cost=€  644.24 , Grid_cost=€  1534.21 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7001.33 , Grid_used_en=KWh  1468.56 , RE-to-vehicle_unused_en=KWh  8469.89 , Total_selling_cost=€  -244.9 , Grid_cost=€  64.48 
 EV_INFO: Av.EV_energy_leaving=kWh  71.95 , Std.EV_energy_leaving=kWh  22.8 , EV_departures =  1040 , EV_queue_left =  0
SCORE:  Cumulative_reward= 405735.33 - Step_rewars (load_t= 347098.0, EVs_energy_t= 32595.73)
 - Final_rewards (Av.EVs_energy= 18425.47, Grid_used_en= -902.76, RE-to-vehicle_unused_en= -3495.62, Grid_cost= 12014.51)
Episode:1 Score:405735.3346775005


In [101]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [102]:
VPP_table.head(15000)

0    1          2          3  \
time                                                        
2022-01-01 00:00:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:15:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:30:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 00:45:00   0.000000  0.0   0.000000   0.000000   
2022-01-01 01:00:00   0.000000  0.0   0.000000   0.000000   
...                        ...  ...        ...        ...   
2022-06-06 04:45:00  64.224586  0.0  99.989998  49.611385   
2022-06-06 05:00:00  65.392715  0.0  99.989998  50.779514   
2022-06-06 05:15:00  66.603065  0.0  99.989998  51.989864   
2022-06-06 05:30:00  66.603065  0.0  99.989998  53.860256   
2022-06-06 05:45:00  66.603065  0.0  99.989998  55.611713   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [17119, 0, 17117, 17118]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [17119, 0, 17117, 17118]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [17119, 0, 17117, 17118]  [0, 2, 1, 1]   
2022-06-06 05:30:00  [17119, 0, 17117, 17118]  [0, 2, 1, 1]   
2022-06-06 05:45:00  [17119, 0, 17117, 17118]  [0, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00   [True, False, False, True]        7.242415   
2022-06-06 05:00:00   [True, False, False, True]        9.345051   
2022-06-06 05:15:00   [True, False, False, True]        9.682819   
2022-06-06 05:30:00   [True, False, False, True]        7.481575   
2022-06-06 05:45:00   [True, False, False, True]        7.005832   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.856821    -5.126466        0.0   
2022-01-01 00:15:00                0.0 -4.139112    -4.203511        0.0   
2022-01-01 00:30:00                0.0 -3.522107    -3.350701        0.0   
2022-01-01 00:45:00                0.0 -3.010421    -5.356846        0.0   
2022-01-01 01:00:00                0.0 -4.392530    -3.609866        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00                0.0 -3.621195    -5.611375        0.0   
2022-06-06 05:00:00                0.0 -4.672512    -5.764906        0.0   
2022-06-06 05:15:00                0.0 -4.841397    -8.165053        0.0   
2022-06-06 05:30:00                0.0 -7.481558    -7.732559        0.0   
2022-06-06 05:45:00                0.0 -7.005815    -8.075435        0.0   

                      rewards  
time                           
2022-01-01 00:00:00 -5.126466  
2022-01-01 00:15:00 -4.203511  
2022-01-01 00:30:00 -3.350701  
2022-01-01 00:45:00 -5.356846  
2022-01-01 01:00:00 -3.609866  
...                       ...  
2022-06-06 04:45:00 -5.611375  
2022-06-06 05:00:00 -5.764906  
2022-06-06 05:15:00 -8.165053  
2022-06-06 05:30:00 -7.732559  
2022-06-06 05:45:00 -8.075435  

[15000 rows x 13 columns]

In [103]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [104]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [105]:
env.plot_VPP_Elvis_comparison()

In [106]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [107]:
env.plot_rewards_stats()

In [108]:
env.plot_EVs_kpi()

In [109]:
env.plot_load_kpi()

In [110]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [111]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 17732, Arrival time: 2022-01-01 00:00:00, Parking_time: 24, Leaving_time: 2022-01-02 00:00:00, SOC: 0.4739870892826944, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 18774, Arrival time: 2022-12-31 20:15:00, Parking_time: 24, Leaving_time: 2023-01-01 20:15:00, SOC: 0.46141696791285525, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en=kWh  1556.25 , RE-to-vehicle_unused_en=kWh  -35673.95 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  9792.1 , Grid_used_en=kWh  32214.05 , RE-to-vehicle_unused_en=kWh  22421.95 , Total_selling_cost=€  525.36 , Grid_cost=€  1344.62 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [112]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [113]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [114]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  7287.92 , Grid_used_en=kWh  30975.82 , RE-to-vehicle_unused_en=kWh  23687.89 , Total_selling_cost=€  441.64 , Grid_cost=€  1314.57 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -9137.58 , Grid_used_en=KWh  956.78 , RE-to-vehicle_unused_en=KWh  10094.36 , Total_selling_cost=€  -320.4 , Grid_cost=€  39.66 
 EV_INFO: Av.EV_energy_leaving=kWh  73.92 , Std.EV_energy_leaving=kWh  21.97 , EV_departures =  1042 , EV_queue_left =  0
SCORE:  Cumulative_reward= 395771.64 - Step_rewars (load_t= 329485.11, EVs_energy_t= 38733.0)
 - Final_rewards (Av.EVs_energy= 17970.22, Grid_used_en= -444.4, RE-to-vehicle_unused_en= -4240.12, Grid_cost= 14267.83)
Episode:1 Score:395771.63921093335


In [115]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [116]:
VPP_table.head(14995)

0          1    2    3            EVs_id       actions  \
time                                                                            
2022-01-01 00:00:00  0.0   0.000000  0.0  0.0      [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00  0.0   0.000000  0.0  0.0      [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00  0.0   0.000000  0.0  0.0      [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00  0.0   0.000000  0.0  0.0      [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-01-01 01:00:00  0.0   0.000000  0.0  0.0      [0, 0, 0, 0]  [2, 0, 1, 0]   
...                  ...        ...  ...  ...               ...           ...   
2022-06-06 03:30:00  0.0  99.989998  0.0  0.0  [0, 20267, 0, 0]  [0, 1, 2, 2]   
2022-06-06 03:45:00  0.0  99.989998  0.0  0.0  [0, 20267, 0, 0]  [0, 1, 2, 2]   
2022-06-06 04:00:00  0.0  99.989998  0.0  0.0  [0, 20267, 0, 0]  [0, 1, 2, 2]   
2022-06-06 04:15:00  0.0  99.989998  0.0  0.0  [0, 20267, 0, 0]  [0, 1, 2, 2]   
2022-06-06 04:30:00  0.0  99.989998  0.0  0.0  [0, 20267, 0, 0]  [0, 1, 2, 2]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00   [False, True, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00   [True, True, False, False]        0.000009   
2022-06-06 03:45:00   [True, True, False, False]        0.000009   
2022-06-06 04:00:00   [True, True, False, False]        0.000009   
2022-06-06 04:15:00   [True, True, False, False]        0.000009   
2022-06-06 04:30:00   [True, True, False, False]        0.000009   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -2.864391    -5.426099        0.0   
2022-01-01 00:15:00                0.0 -4.468709    -3.622251        0.0   
2022-01-01 00:30:00                0.0 -3.173351    -4.856589        0.0   
2022-01-01 00:45:00                0.0 -3.913953    -5.792848        0.0   
2022-01-01 01:00:00                0.0 -4.872133    -6.533104        0.0   
...                                ...       ...          ...        ...   
2022-06-06 03:30:00                0.0 -4.166695    -4.550525        0.0   
2022-06-06 03:45:00                0.0 -3.730315    -7.079945        0.0   
2022-06-06 04:00:00                0.0 -6.287939    -8.243358        0.0   
2022-06-06 04:15:00                0.0 -7.567694    -7.130774        0.0   
2022-06-06 04:30:00                0.0 -6.343851    -7.401052        0.0   

                      rewards  
time                           
2022-01-01 00:00:00 -5.426099  
2022-01-01 00:15:00 -3.622251  
2022-01-01 00:30:00 -4.856589  
2022-01-01 00:45:00 -5.792848  
2022-01-01 01:00:00 -6.533104  
...                       ...  
2022-06-06 03:30:00 -4.550525  
2022-06-06 03:45:00 -7.079945  
2022-06-06 04:00:00 -8.243358  
2022-06-06 04:15:00 -7.130774  
2022-06-06 04:30:00 -7.401052  

[14995 rows x 13 columns]

In [117]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [118]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [119]:
env.plot_VPP_Elvis_comparison()

In [120]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [121]:
env.plot_rewards_stats()

In [122]:
env.plot_EVs_kpi()

In [123]:
env.plot_actions_kpi()

In [124]:
env.plot_load_kpi()

In [125]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [126]:
#env.close()